<a href="https://colab.research.google.com/github/rmwvamp/ECGNotebooks/blob/main/FinalECGFeatureExtractionCode_CLASDataset_Allfiles_SingleCode.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Drive Mounting and Dependencies

In [ ]:
from google.colab import drive
drive.mount('/gdrive')
%cd /gdrive

Drive already mounted at /gdrive; to attempt to forcibly remount, call drive.mount("/gdrive", force_remount=True).
/gdrive


In [ ]:
%cd /gdrive/MyDrive/SamsungWork/Participant2Data

/gdrive/MyDrive/SamsungWork/Participant2Data


In [ ]:
!pip install wfdb
!pip install opensignalsreader
!pip install pyhrv
!pip install biosppy
!pip install pyhrv

In [ ]:
import os
import sys
import csv

#median
import statistics
from statistics import median

import os
from glob import glob

# data science
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.patches import Ellipse
import seaborn as sns

# signal processing
from scipy import signal
from scipy.ndimage import label
from scipy.stats import zscore
from scipy.interpolate import interp1d
from scipy.integrate import trapz

# physionet data
import wfdb
from wfdb import processing

import numpy as np
import pandas as pd
pd.set_option('display.max_colwidth',100000)


# Feature Function Declaration

## Function for Logic Part

In [ ]:
def get_plot_ranges(start=0, end=150, n=2.5):
    '''
    Make an iterator that divides into n or n+1 ranges. 
    - if end-start is divisible by steps, return n ranges
    - if end-start is not divisible by steps, return n+1 ranges, where the last range is smaller and ends at n
    
    # Example:
    >> list(get_plot_ranges())
    >> [(0.0, 3.0), (3.0, 6.0), (6.0, 9.0)]

    '''
    distance = end - start
    for i in np.arange(start, end, np.floor(distance/n)):
        yield (int(i), int(np.minimum(end, np.floor(distance/n) + i)))

def group_peaks(p, threshold=5):
    '''
    The peak detection algorithm finds multiple peaks for each QRS complex. 
    Here we group collections of peaks that are very near (within threshold) and we take the median index 
    '''
    # initialize output
    output = np.empty(0)

    # label groups of sample that belong to the same peak
    peak_groups, num_groups = label(np.diff(p) < threshold)

    # iterate through groups and take the mean as peak index
    for i in np.unique(peak_groups)[1:]:
        peak_group = p[np.where(peak_groups == i)]
        output = np.append(output, np.median(peak_group))
    return output

def detect_peaks(ecg_signal, threshold=0.3, qrs_filter=None):
    '''
    Peak detection algorithm using cross corrrelation and threshold 
    '''
    if qrs_filter is None:
        # create default qrs filter
        t = np.linspace(1.5 * np.pi, 3.5 * np.pi, 15)
        qrs_filter = np.sin(t)
    
    # normalize data
    ecg_signal = (ecg_signal - ecg_signal.mean()) / ecg_signal.std()

    # calculate cross correlation
    similarity = np.correlate(ecg_signal, qrs_filter, mode="same")
    similarity = similarity / np.max(similarity)

    # return peaks (values in ms) using threshold
    return ecg_signal[similarity > threshold].index, similarity


def get_rr_corrected(df):
  # detect peaks
  peaks, similarity = detect_peaks(df.ecg2, threshold=0.3)

  # group peaks so we get a single peak per beat (hopefully)
  grouped_peaks = group_peaks(peaks)

  # RR-intervals are the differences between successive peaks
  rr = np.diff(grouped_peaks)

  rr_corrected = rr.copy()
  rr_corrected[np.abs(zscore(rr)) > 2] = np.median(rr)
  return rr_corrected

def plot_rr_corrected(rr_corrected,rr):

  plt.title("RR-intervals", fontsize=24)
  plt.xlabel("Time (ms)", fontsize=16)
  plt.ylabel("RR-interval (ms)", fontsize=16)

  plt.plot(rr, color="red", linewidth=1, label="RR-intervals")
  plt.plot(rr_corrected, color="green", linewidth=2, label="RR-intervals after correction")
  plt.legend(fontsize=20)

def timedomain(rr):

  results = {}
  
  hr = 60000/rr
  
  # mean RR-interval
  results['Mean RR (ms)'] = np.mean(rr)
  results['STD RR/SDNN (ms)'] = np.std(rr)
  results['Mean HR (Kubios\' style) (beats/min)'] = 60000/np.mean(rr)
  results['Mean HR (beats/min)'] = np.mean(hr)
  results['STD HR (beats/min)'] = np.std(hr)
  results['Min HR (beats/min)'] = np.min(hr)
  results['Max HR (beats/min)'] = np.max(hr)
  results['RMSSD (ms)'] = np.sqrt(np.mean(np.square(np.diff(rr))))
  results['NNxx'] = np.sum(np.abs(np.diff(rr)) > 50)*1
  results['pNNxx (%)'] = 100 * np.sum((np.abs(np.diff(rr)) > 50)*1) / len(rr)
  # print("Time domain metrics - automatically corrected RR-intervals:")
  # for k, v in results.items():
  #     print("- %s: %.2f" % (k, v))
  return results

def frequency_domain(rr, fs=4):     #4

  # sample rate for interpolation
  steps = 1 / fs

  # create interpolation function based on the rr-samples. 
  x = np.cumsum(rr) / 1000.0
  f = interp1d(x, rr, kind='cubic',fill_value="extrapolate")

  # now we can sample from interpolation function
  xx = np.arange(1, np.max(x), steps)
  rr_interpolated = f(xx)
  # Estimate the spectral density using Welch's method
  fxx, pxx = signal.welch(x=rr_interpolated, fs=fs)
  
  '''
  Segement found frequencies in the bands 
    - Very Low Frequency (VLF): 0-0.04Hz 
    - Low Frequency (LF): 0.04-0.15Hz 
    - High Frequency (HF): 0.15-0.4Hz
  '''
  cond_vlf = (fxx >= 0) & (fxx < 0.04)
  cond_lf = (fxx >= 0.04) & (fxx < 0.15)
  cond_hf = (fxx >= 0.15) & (fxx < 0.4)
  
  # calculate power in each band by integrating the spectral density 
  vlf = trapz(pxx[cond_vlf], fxx[cond_vlf])
  lf = trapz(pxx[cond_lf], fxx[cond_lf])
  hf = trapz(pxx[cond_hf], fxx[cond_hf])
  
  # sum these up to get total power
  total_power = vlf + lf + hf

  # find which frequency has the most power in each band
  peak_vlf = fxx[cond_vlf][np.argmax(pxx[cond_vlf])]
  peak_lf = fxx[cond_lf][np.argmax(pxx[cond_lf])]
  peak_hf = fxx[cond_hf][np.argmax(pxx[cond_hf])]

  # fraction of lf and hf
  lf_nu = 100 * lf / (lf + hf)
  hf_nu = 100 * hf / (lf + hf)
  
  results = {}
  results['Power VLF (ms2)'] = vlf
  results['Power LF (ms2)'] = lf
  results['Power HF (ms2)'] = hf   
  results['Power Total (ms2)'] = total_power

  results['LF/HF'] = (lf/hf)
  results['Peak VLF (Hz)'] = peak_vlf
  results['Peak LF (Hz)'] = peak_lf
  results['Peak HF (Hz)'] = peak_hf

  results['Fraction LF (nu)'] = lf_nu
  results['Fraction HF (nu)'] = hf_nu
  
  # print("Frequency domain metrics:")
  # for k, v in results.items():
  #     print("- %s: %.2f" % (k, v))
  return results, fxx, pxx
def get_rr_corrected_ourdata(df):
  # detect peaks
  t = np.linspace(1.5 * np.pi, 3.5 * np.pi,13)
  qrs_filter = -np.sin(t)
  peaks, similarity = detect_peaks(df.ecg2, threshold=0.03,qrs_filter=qrs_filter)
 
  # group peaks so we get a single peak per beat (hopefully)
  grouped_peaks = group_peaks(peaks,threshold=3)
  # print(grouped_peaks)

  final=[element * 65 for element in grouped_peaks] 
  # print(final)
  # RR-intervals are the differences between successive peaks
  rr = np.diff(final)

  rr_corrected = rr.copy()
  rr_corrected[np.abs(zscore(rr)) > 2] = np.median(rr)
  return rr_corrected

def labeler(df,labelling_criteria):
   df = df.apply(lambda x : True
            if x['ecg2'] >labelling_criteria else False, axis = 1)
   value = len(df[df==True])
   print(df)
   if value < 30:
     label= 0
   elif(value > 435):
     label =  1
   else:
     label = -1
   print(value)
   return label


def windowing(df,result_df,labelling_criteria=5):
  df1=df.rolling(window=1280)
  type(df1)
  i=1
  j=0
  for df2 in df1:
    if len(df2)>=1280 and i%int(1280/2)==0:
#       print((df2))
      results_td=[]
      results_fd=[]
      results=[]
      rr_corrected= get_rr_corrected_ourdata(df2)
      # plot_rr_corrected(rr_corrected)
      # print(rr_corrected)
      results_td=timedomain(rr_corrected)
      # print(results_td)
      results_fd, fxx, pxx =frequency_domain(rr_corrected)
      # print(results_fd)
      results={**results_td,**results_fd}
      label=labeler(df2,labelling_criteria)
      if label==-1:
        i+=1
        continue
      # results['stress_level']=label
      # print(results)
      result_df=result_df.append(results,ignore_index=True)
      # print(result_df)
      i+=1
      j+=1
    else:
      i+=1
  return result_df

## Function for Feature Extraction

In [ ]:
def baseline_stress_features(input_path=r"/gdrive/MyDrive/Class_Dataset/CLAS Dataset/Participants/Part4",output_path=r"/gdrive/MyDrive/SamsungWork/ECGFeatures10Seconds_1May22",partnumber="Part4"):
  %cd "$input_path"  
  # File setup for baseline dataframe
  baseline_file=['1_ecg_.csv','4_ecg_.csv','7_ecg_.csv','10_ecg_.csv']
  baseline_df=pd.read_csv(os.path.join(input_path,baseline_file[0]))
  column_names=['Mean RR (ms)', 'STD RR/SDNN (ms)', "Mean HR (Kubios' style) (beats/min)", 'Mean HR (beats/min)', 'STD HR (beats/min)', 'Min HR (beats/min)', 'Max HR (beats/min)', 'RMSSD (ms)', 'NNxx', 'pNNxx (%)', 'Power VLF (ms2)', 'Power LF (ms2)', 'Power HF (ms2)', 'Power Total (ms2)', 'LF/HF', 'Peak VLF (Hz)', 'Peak LF (Hz)', 'Peak HF (Hz)', 'Fraction LF (nu)', 'Fraction HF (nu)']
  # column_names=['Mean_RR', 'STD_RR_SDNN_Ratio', "Mean_HR_Kubios", 'Mean_HR', 'STD_HR', 'Min_HR', 'Max_HR', 'RMSSD', 'NNxx', 'pNNxx', 'Power_VLF', 'Power_LF', 'Power_HF', 'Power_Total', 'LF/HF', 'Peak_VLF', 'Peak_LF', 'Peak_HF', 'Fraction_LF', 'Fraction_HF']
  result_baseline_df= pd.DataFrame(columns=column_names) 

 # File setup for stress dataframe
  stress_df=pd.read_csv('2_ecg_mathtest.csv')
  data=pd.read_csv('8_ecg_IQtest.csv')
  stress_df=stress_df.append(data,ignore_index=True)

  result_stress_df= pd.DataFrame(columns=column_names)

  # removing unnecessary columns
  baseline_df=baseline_df.drop(['Timestamp','ecg1','PythonTimestamp'],axis=1)
  stress_df=stress_df.drop(['Timestamp','ecg1','PythonTimestamp'],axis=1)

  # appending baselinedataframe, adding all data baseline together
  for base in baseline_file[1:]:
    data=pd.read_csv(base)
    baseline_df=baseline_df.append(data,ignore_index=True)

  labelling_criteria=0

  # setting up folders for saving
  if not os.path.exists(os.path.join(output_path,partnumber,"output",str(labelling_criteria))):
    os.makedirs(os.path.join(output_path,partnumber,"output",str(labelling_criteria)))

  # baseline feature extraction
  print(baseline_df)
  result_baseline_df=windowing(baseline_df[:],result_baseline_df,labelling_criteria)
  # result_baseline_df=windowing(baseline_df[15360:30719],result_baseline_df,labelling_criteria)
  # result_baseline_df=windowing(baseline_df[30720:38408],result_baseline_df,labelling_criteria)
  result_baseline_df['stress_level']=0;
  result_baseline_df.to_csv(os.path.join(output_path,partnumber,"output",str(labelling_criteria),"baseline.csv"))
  print(result_baseline_df)

   # stress feature extraction
  # %%capture
  print(stress_df)
  result_stress_df=windowing(stress_df[:],result_stress_df,labelling_criteria)
  # result_stress_df=windowing(stress_df[15360:30719],result_stress_df,labelling_criteria)
  # result_stress_df=windowing(stress_df[30720:46079],result_stress_df,labelling_criteria)
  # result_stress_df=windowing(stress_df[46080:61439],result_stress_df,labelling_criteria)
  # result_stress_df=windowing(stress_df[61440:76799],result_stress_df,labelling_criteria)
  # result_stress_df=windowing(stress_df[76780:92139],result_stress_df,labelling_criteria)
  # result_stress_df=windowing(stress_df[92140:107499],result_stress_df,labelling_criteria)
  # result_stress_df=windowing(stress_df[107450:120252],result_stress_df,labelling_criteria)

  result_stress_df['stress_level']=1;
  result_stress_df.to_csv(os.path.join(output_path,partnumber,"output",str(labelling_criteria),"stress.csv"))
  print(result_stress_df)
  # print(partnumber)

  print("Feature Extracted for %s saved at %s " %(partnumber,os.path.join(output_path,partnumber)))

In [ ]:
# def baseline_stress_features(input_path=r"/gdrive/MyDrive/Class_Dataset/CLAS Dataset/Participants/Part4",output_path=r"/gdrive/MyDrive/SamsungWork/ECGFeatures10Seconds_1May22",partnumber="Part4"):
#   %cd "$input_path"  
#   # File setup for baseline dataframe
#   baseline_file=['1_ecg_.csv','4_ecg_.csv','7_ecg_.csv','10_ecg_.csv']
#   baseline_df=pd.read_csv(os.path.join(input_path,baseline_file[0]))
#   # column_names=['Mean RR (ms)', 'STD RR/SDNN (ms)', "Mean HR (Kubios' style) (beats/min)", 'Mean HR (beats/min)', 'STD HR (beats/min)', 'Min HR (beats/min)', 'Max HR (beats/min)', 'RMSSD (ms)', 'NNxx', 'pNNxx (%)', 'Power VLF (ms2)', 'Power LF (ms2)', 'Power HF (ms2)', 'Power Total (ms2)', 'LF/HF', 'Peak VLF (Hz)', 'Peak LF (Hz)', 'Peak HF (Hz)', 'Fraction LF (nu)', 'Fraction HF (nu)','stress_level']
#   column_names=['Mean_RR', 'STD_RR_SDNN_Ratio', "Mean_HR_Kubios", 'Mean_HR', 'STD_HR', 'Min_HR', 'Max_HR', 'RMSSD', 'NNxx', 'pNNxx', 'Power_VLF', 'Power_LF', 'Power_HF', 'Power_Total', 'LF/HF', 'Peak_VLF', 'Peak_LF', 'Peak_HF', 'Fraction_LF', 'Fraction_HF']
#   result_baseline_df= pd.DataFrame(columns=column_names) 

#  # File setup for stress dataframe
#   stress_df=pd.read_csv('2_ecg_mathtest.csv')
#   data=pd.read_csv('8_ecg_IQtest.csv')
#   stress_df=stress_df.append(data,ignore_index=True)

#   result_stress_df= pd.DataFrame(columns=column_names)

#   # removing unnecessary columns
#   baseline_df=baseline_df.drop(['Timestamp','ecg1','PythonTimestamp'],axis=1)
#   stress_df=stress_df.drop(['Timestamp','ecg1','PythonTimestamp'],axis=1)

#   # appending baselinedataframe, adding all data baseline together
#   for base in baseline_file[1:]:
#     data=pd.read_csv(base)
#     baseline_df=baseline_df.append(data,ignore_index=True)

#   labelling_criteria=0

#   # setting up folders for saving
#   if not os.path.exists(os.path.join(output_path,partnumber,"output",str(labelling_criteria))):
#     os.makedirs(os.path.join(output_path,partnumber,"output",str(labelling_criteria)))

#   # baseline feature extraction
#   print(baseline_df)
#   result_baseline_df=windowing(baseline_df[:15359],result_baseline_df,labelling_criteria)
#   result_baseline_df=windowing(baseline_df[15360:30719],result_baseline_df,labelling_criteria)
#   result_baseline_df=windowing(baseline_df[30720:38408],result_baseline_df,labelling_criteria)
#   result_baseline_df.to_csv(os.path.join(output_path,partnumber,"output",str(labelling_criteria),"baseline.csv"))
#   print(result_baseline_df)

#    # stress feature extraction
#   # %%capture
#   print(stress_df)
#   result_stress_df=windowing(stress_df[:15359],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[15360:30719],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[30720:46079],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[46080:61439],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[61440:76799],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[76780:92139],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[92140:107499],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[107450:120252],result_stress_df,labelling_criteria)

#   result_stress_df.to_csv(os.path.join(output_path,partnumber,"output",str(labelling_criteria),"stress.csv"))
#   print(result_stress_df)
#   # print(partnumber)

#   print("Feature Extracted for %s saved at %s " %(partnumber,os.path.join(output_path,partnumber)))

In [ ]:
# def baseline_stress_features(input_path=r"/gdrive/MyDrive/Class_Dataset/CLAS Dataset/Participants/Part4",output_path=r"/gdrive/MyDrive/SamsungWork/ECGFeatures10Seconds_1May22",partnumber="Part4"):
#   %cd "$input_path"  
#   # File setup for baseline dataframe
#   baseline_file=['1_ecg_.csv','4_ecg_.csv','7_ecg_.csv','10_ecg_.csv']
#   baseline_df=pd.read_csv(os.path.join(input_path,baseline_file[0]))
#   column_names=['Mean RR (ms)', 'STD RR/SDNN (ms)', "Mean HR (Kubios' style) (beats/min)", 'Mean HR (beats/min)', 'STD HR (beats/min)', 'Min HR (beats/min)', 'Max HR (beats/min)', 'RMSSD (ms)', 'NNxx', 'pNNxx (%)', 'Power VLF (ms2)', 'Power LF (ms2)', 'Power HF (ms2)', 'Power Total (ms2)', 'LF/HF', 'Peak VLF (Hz)', 'Peak LF (Hz)', 'Peak HF (Hz)', 'Fraction LF (nu)', 'Fraction HF (nu)','stress_level']
#   # column_names=['Mean_RR', 'STD_RR_SDNN_Ratio', "Mean_HR_Kubios", 'Mean_HR', 'STD_HR', 'Min_HR', 'Max_HR', 'RMSSD', 'NNxx', 'pNNxx', 'Power_VLF', 'Power_LF', 'Power_HF', 'Power_Total', 'LF/HF', 'Peak_VLF', 'Peak_LF', 'Peak_HF', 'Fraction_LF', 'Fraction_HF']
#   result_baseline_df= pd.DataFrame(columns=column_names) 

#  # File setup for stress dataframe
#   stress_df=pd.read_csv('2_ecg_mathtest.csv')
#   data=pd.read_csv('8_ecg_IQtest.csv')
#   stress_df=stress_df.append(data,ignore_index=True)

#   result_stress_df= pd.DataFrame(columns=column_names)

#   # removing unnecessary columns
#   baseline_df=baseline_df.drop(['Timestamp','ecg1','PythonTimestamp'],axis=1)
#   stress_df=stress_df.drop(['Timestamp','ecg1','PythonTimestamp'],axis=1)

#   # appending baselinedataframe, adding all data baseline together
#   for base in baseline_file[1:]:
#     data=pd.read_csv(base)
#     baseline_df=baseline_df.append(data,ignore_index=True)

#   labelling_criteria=0

#   # setting up folders for saving
#   if not os.path.exists(os.path.join(output_path,partnumber,"output",str(labelling_criteria))):
#     os.makedirs(os.path.join(output_path,partnumber,"output",str(labelling_criteria)))

#   # baseline feature extraction
#   print(baseline_df)
#   result_baseline_df=windowing(baseline_df[:7679],result_baseline_df,labelling_criteria)
#   result_baseline_df=windowing(baseline_df[7680:15359],result_baseline_df,labelling_criteria)
#   result_baseline_df=windowing(baseline_df[15360:23039],result_baseline_df,labelling_criteria)
#   result_baseline_df=windowing(baseline_df[23040:30719],result_baseline_df,labelling_criteria)
#   result_baseline_df=windowing(baseline_df[30720:38399],result_baseline_df,labelling_criteria)
#   # result_baseline_df=windowing(baseline_df[38400:38408],result_baseline_df,labelling_criteria)
#   result_baseline_df.to_csv(os.path.join(output_path,partnumber,"output",str(labelling_criteria),"baseline.csv"))
#   print(result_baseline_df)

#    # stress feature extraction
#   # %%capture
#   print(stress_df)
#   result_stress_df=windowing(stress_df[:7679],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[7680:15359],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[15360:23039],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[23040:30719],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[30720:38399],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[38400:46079],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[46080:53759],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[53760:61439],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[61440:69119],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[69120:76799],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[76800:84479],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[84480:92159],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[92160:99839],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[99840:107519],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[107520:115199],result_stress_df,labelling_criteria)
#   result_stress_df=windowing(stress_df[115200:120252],result_stress_df,labelling_criteria)

#   result_stress_df.to_csv(os.path.join(output_path,partnumber,"output",str(labelling_criteria),"stress.csv"))
#   print(result_stress_df)
#   # print(partnumber)

#   print("Feature Extracted for %s saved at %s " %(partnumber,os.path.join(output_path,partnumber)))

# Running Function on all Files

In [ ]:
Participants=['Part1','Part2','Part3','Part4','Part5','Part6','Part7','Part8','Part9','Part10','Part11','Part12','Part13','Part14','Part15','Part16','Part17','Part18','Part19','Part20','Part21','Part22','Part23','Part24','Part25','Part26','Part27','Part28','Part29','Part30','Part31','Part32','Part33','Part34','Part35','Part36','Part37','Part38','Part39','Part40','Part41','Part42','Part43','Part44','Part45','Part46','Part47','Part48','Part49','Part50','Part51','Part52','Part53','Part54','Part55','Part56','Part57','Part58','Part59','Part60']

In [ ]:
Working_Participants=['Part2','Part4','Part5','Part8','Part10','Part11','Part12','Part17','Part21','Part23','Part24','Part26','Part27','Part28','Part29','Part30','Part31','Part32','Part33','Part34','Part35','Part36','Part38','Part39','Part40','Part41','Part42','Part43','Part44','Part45','Part46','Part47','Part48','Part49','Part51','Part53','Part54','Part55','Part56','Part57','Part58','Part59','Part60']

In [ ]:
Working_Participants1=['Part4','Part5','Part8','Part10','Part11','Part12','Part17','Part21','Part23','Part24','Part26','Part27','Part28','Part29','Part30','Part31','Part32','Part33','Part34','Part35','Part36','Part38','Part39','Part40','Part41','Part42','Part43','Part44','Part45','Part46','Part47','Part48','Part49','Part51','Part53','Part54','Part55','Part56','Part57','Part58','Part59','Part60']

In [ ]:
Error_Participants=['Part1','Part3','Part6','Part7','Part9','Part13','Part14','Part15','Part16','Part18','Part19','Part20','Part22','Part25','Part37','Part50','Part52']
print(len(Error_Participants))

17


In [ ]:
New_Participants10=['Part4','Part5','Part6','Part10','Part11','Part12','Part14','Part15','Part17','Part23','Part24','Part26','Part27','Part28','Part30','Part31','Part32','Part33','Part34','Part35','Part36','Part38','Part39','Part40','Part42','Part43','Part44','Part45','Part46','Part47','Part48','Part49','Part51','Part53','Part54','Part55','Part56','Part57','Part58','Part59','Part60']

In [ ]:
Error_Participants10=['Part1','Part2','Part3','Part7','Part8','Part9','Part13','Part16','Part18','Part19','Part20','Part21','Part22','Part25','Part29','Part37','Part41','Part50','Part52']

In [ ]:
Participants_5=['Part4','Part5','Part6','Part8','Part10','Part11','Part14','Part15','Part17','Part23','Part24','Part26','Part27','Part28','Part31','Part32','Part33','Part34','Part35','Part36','Part39','Part40','Part42','Part43','Part44','Part45','Part46','Part47','Part48','Part49','Part51','Part52','Part53','Part54','Part55','Part56','Part57','Part58','Part59','Part60']

In [ ]:
ErrorParticipants_5=['Part1','Part2','Part3','Part7','Part12','Part13','Part16','Part18','Part19','Part20','Part21','Part22','Part25','Part29','Part30','Part37','Part38','Part41','Part50']

In [ ]:
# Participants=['Part45','Part46','Part47','Part48','Part49','Part50','Part51','Part52','Part53','Part54','Part55','Part56','Part57','Part58','Part59','Part60']51-33

In [ ]:
# for Part in Error_Participants:
#     baseline_stress_features(os.path.join(r"/gdrive/MyDrive/Class_Dataset/CLAS Dataset/Participants", Part,"by_block"),r"/gdrive/MyDrive/SamsungWork/ExtractedFeatures",Part)

In [ ]:
# baseline_stress_features()30->49

In [ ]:
for Part in Participants_5[:]:
    baseline_stress_features(os.path.join(r"/gdrive/MyDrive/Class_Dataset/CLAS Dataset/Participants", Part,"by_block"),r"/gdrive/MyDrive/SamsungWork/ECGFeatures5Seconds_2_60SecondWindowing",Part)

/gdrive/.shortcut-targets-by-id/1oRmZOKPo1r153R8uQckeuhxEs5K25BXY/Class_Dataset/CLAS Dataset/Participants/Part4/by_block
           ecg2  Timestamp  PythonTimestamp        ecg1
0      2.448674        NaN              NaN         NaN
1      2.238223        NaN              NaN         NaN
2      2.207210        NaN              NaN         NaN
3      2.516468        NaN              NaN         NaN
4      2.974512        NaN              NaN         NaN
...         ...        ...              ...         ...
22859  1.327471  8622747.0     1.551787e+09 -605.000072
22860  1.095239  8622875.0     1.551787e+09 -605.000072
22861  0.908660  8623003.0     1.551787e+09 -605.000072
22862  1.115289  8623131.0     1.551787e+09 -605.000072
22863  1.369445  8623259.0     1.551787e+09 -605.000072

[22864 rows x 4 columns]
0       True
1       True
2       True
3       True
4       True
        ... 
1275    True
1276    True
1277    True
1278    True
1279    True
Length: 1280, dtype: bool
1280
640    

/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 253, using nperseg = 253
  .format(nperseg, input_length))


5760    True
5761    True
5762    True
5763    True
5764    True
        ... 
7035    True
7036    True
7037    True
7038    True
7039    True
Length: 1280, dtype: bool
1280
6400    True
6401    True
6402    True
6403    True
6404    True
        ... 
7675    True
7676    True
7677    True
7678    True
7679    True
Length: 1280, dtype: bool
1260
7040    True
7041    True
7042    True
7043    True
7044    True
        ... 
8315    True
8316    True
8317    True
8318    True
8319    True
Length: 1280, dtype: bool
1249
7680    True
7681    True
7682    True
7683    True
7684    True
        ... 
8955    True
8956    True
8957    True
8958    True
8959    True
Length: 1280, dtype: bool
1179
8320     True
8321     True
8322     True
8323    False
8324     True
        ...  
9595     True
9596     True
9597     True
9598     True
9599     True
Length: 1280, dtype: bool
1190


/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 192, using nperseg = 192
  .format(nperseg, input_length))
/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 219, using nperseg = 219
  .format(nperseg, input_length))
/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 251, using nperseg = 251
  .format(nperseg, input_length))


8960     True
8961     True
8962     True
8963     True
8964     True
         ... 
10235    True
10236    True
10237    True
10238    True
10239    True
Length: 1280, dtype: bool
1280
9600     True
9601     True
9602     True
9603     True
9604     True
         ... 
10875    True
10876    True
10877    True
10878    True
10879    True
Length: 1280, dtype: bool
1280
10240    True
10241    True
10242    True
10243    True
10244    True
         ... 
11515    True
11516    True
11517    True
11518    True
11519    True
Length: 1280, dtype: bool
1280
10880    True
10881    True
10882    True
10883    True
10884    True
         ... 
12155    True
12156    True
12157    True
12158    True
12159    True
Length: 1280, dtype: bool
1280
11520    True
11521    True
11522    True
11523    True
11524    True
         ... 
12795    True
12796    True
12797    True
12798    True
12799    True
Length: 1280, dtype: bool
1280
12160     True
12161     True
12162     True
12163     True
12164     True


...

15360    True
15361    True
15362    True
15363    True
15364    True
         ... 
16635    True
16636    True
16637    True
16638    True
16639    True
Length: 1280, dtype: bool
1280
16000    True
16001    True
16002    True
16003    True
16004    True
         ... 
17275    True
17276    True
17277    True
17278    True
17279    True
Length: 1280, dtype: bool
1280
16640    True
16641    True
16642    True
16643    True
16644    True
         ... 
17915    True
17916    True
17917    True
17918    True
17919    True
Length: 1280, dtype: bool
1280
17280    True
17281    True
17282    True
17283    True
17284    True
         ... 
18555    True
18556    True
18557    True
18558    True
18559    True
Length: 1280, dtype: bool
1280
17920    True
17921    True
17922    True
17923    True
17924    True
         ... 
19195    True
19196    True
19197    True
19198    True
19199    True
Length: 1280, dtype: bool
1280
18560    True
18561    True
18562    True
18563    True
18564    True
     

/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 222, using nperseg = 222
  .format(nperseg, input_length))
/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 213, using nperseg = 213
  .format(nperseg, input_length))


2560    True
2561    True
2562    True
2563    True
2564    True
        ... 
3835    True
3836    True
3837    True
3838    True
3839    True
Length: 1280, dtype: bool
1280
3200     True
3201     True
3202     True
3203     True
3204     True
        ...  
4475    False
4476    False
4477    False
4478    False
4479    False
Length: 1280, dtype: bool
934
3840     True
3841     True
3842     True
3843     True
3844     True
        ...  
5115    False
5116    False
5117    False
5118    False
5119    False
Length: 1280, dtype: bool
294
4480    False
4481    False
4482    False
4483    False
4484    False
        ...  
5755    False
5756    False
5757    False
5758    False
5759    False
Length: 1280, dtype: bool
0
5120    False
5121    False
5122    False
5123    False
5124    False
        ...  
6395    False
6396    False
6397    False
6398    False
6399    False
Length: 1280, dtype: bool
0
5760    False
5761    False
5762    False
5763    False
5764    False
        ...  
7035    Fa

/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 117, using nperseg = 117
  .format(nperseg, input_length))
/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 143, using nperseg = 143
  .format(nperseg, input_length))


ValueError: ignored

# 5 Seconds Window, 2.5 Overlapping

In [ ]:
Participants5=['Part4','Part5','Part6','Part8','Part10','Part11','Part14','Part17','Part24','Part26','Part28','Part31','Part32','Part33','Part34','Part35','Part36','Part39','Part40','Part42','Part43','Part44','Part45','Part46','Part48','Part49','Part51','Part52','Part53','Part54','Part55','Part57','Part58','Part60']

In [ ]:
Error_5=['Part1','Part2','Part3','Part7','Part9','Part12','Part13','Part15','Part16','Part18','Part19','Part20','Part21','Part22','Part23','Part25','Part27','Part29','Part30','Part37','Part38','Part41','Part47','Part50','Part56','Part59']

In [ ]:
# 29->55

In [ ]:
for Part in Participants5[:]:
    baseline_stress_features(os.path.join(r"/gdrive/MyDrive/Class_Dataset/CLAS Dataset/Participants", Part,"by_block"),r"/gdrive/MyDrive/SamsungWork/FinalECGFeatures5SecondsCompleteDF",Part)

/gdrive/.shortcut-targets-by-id/1oRmZOKPo1r153R8uQckeuhxEs5K25BXY/Class_Dataset/CLAS Dataset/Participants/Part4/by_block
           ecg2  Timestamp  PythonTimestamp        ecg1
0      2.448674        NaN              NaN         NaN
1      2.238223        NaN              NaN         NaN
2      2.207210        NaN              NaN         NaN
3      2.516468        NaN              NaN         NaN
4      2.974512        NaN              NaN         NaN
...         ...        ...              ...         ...
22859  1.327471  8622747.0     1.551787e+09 -605.000072
22860  1.095239  8622875.0     1.551787e+09 -605.000072
22861  0.908660  8623003.0     1.551787e+09 -605.000072
22862  1.115289  8623131.0     1.551787e+09 -605.000072
22863  1.369445  8623259.0     1.551787e+09 -605.000072

[22864 rows x 4 columns]
0       True
1       True
2       True
3       True
4       True
        ... 
1275    True
1276    True
1277    True
1278    True
1279    True
Length: 1280, dtype: bool
1280
640    

/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 253, using nperseg = 253
  .format(nperseg, input_length))
/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 192, using nperseg = 192
  .format(nperseg, input_length))


5760    True
5761    True
5762    True
5763    True
5764    True
        ... 
7035    True
7036    True
7037    True
7038    True
7039    True
Length: 1280, dtype: bool
1280
6400    True
6401    True
6402    True
6403    True
6404    True
        ... 
7675    True
7676    True
7677    True
7678    True
7679    True
Length: 1280, dtype: bool
1260
7040    True
7041    True
7042    True
7043    True
7044    True
        ... 
8315    True
8316    True
8317    True
8318    True
8319    True
Length: 1280, dtype: bool
1249
7680    True
7681    True
7682    True
7683    True
7684    True
        ... 
8955    True
8956    True
8957    True
8958    True
8959    True
Length: 1280, dtype: bool
1179
8320     True
8321     True
8322     True
8323    False
8324     True
        ...  
9595     True
9596     True
9597     True
9598     True
9599     True
Length: 1280, dtype: bool
1190


/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 219, using nperseg = 219
  .format(nperseg, input_length))
/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 251, using nperseg = 251
  .format(nperseg, input_length))


8960     True
8961     True
8962     True
8963     True
8964     True
         ... 
10235    True
10236    True
10237    True
10238    True
10239    True
Length: 1280, dtype: bool
1280
9600     True
9601     True
9602     True
9603     True
9604     True
         ... 
10875    True
10876    True
10877    True
10878    True
10879    True
Length: 1280, dtype: bool
1280
10240    True
10241    True
10242    True
10243    True
10244    True
         ... 
11515    True
11516    True
11517    True
11518    True
11519    True
Length: 1280, dtype: bool
1280
10880    True
10881    True
10882    True
10883    True
10884    True
         ... 
12155    True
12156    True
12157    True
12158    True
12159    True
Length: 1280, dtype: bool
1280


...

8960     True
8961     True
8962     True
8963     True
8964     True
         ... 
10235    True
10236    True
10237    True
10238    True
10239    True
Length: 1280, dtype: bool
1280
9600     True
9601     True
9602     True
9603     True
9604     True
         ... 
10875    True
10876    True
10877    True
10878    True
10879    True
Length: 1280, dtype: bool
1280
10240    True
10241    True
10242    True
10243    True
10244    True
         ... 
11515    True
11516    True
11517    True
11518    True
11519    True
Length: 1280, dtype: bool
1280
10880    True
10881    True
10882    True
10883    True
10884    True
         ... 
12155    True
12156    True
12157    True
12158    True
12159    True
Length: 1280, dtype: bool
1280
11520    True
11521    True
11522    True
11523    True
11524    True
         ... 
12795    True
12796    True
12797    True
12798    True
12799    True
Length: 1280, dtype: bool
1280
12160    True
12161    True
12162    True
12163    True
12164    True
     

/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 235, using nperseg = 235
  .format(nperseg, input_length))


24320    True
24321    True
24322    True
24323    True
24324    True
         ... 
25595    True
25596    True
25597    True
25598    True
25599    True
Length: 1280, dtype: bool
1280
24960    True
24961    True
24962    True
24963    True
24964    True
         ... 
26235    True
26236    True
26237    True
26238    True
26239    True
Length: 1280, dtype: bool
1280
25600    True
25601    True
25602    True
25603    True
25604    True
         ... 
26875    True
26876    True
26877    True
26878    True
26879    True
Length: 1280, dtype: bool
1280
26240    True
26241    True
26242    True
26243    True
26244    True
         ... 
27515    True
27516    True
27517    True
27518    True
27519    True
Length: 1280, dtype: bool
1280
26880    True
26881    True
26882    True
26883    True
26884    True
         ... 
28155    True
28156    True
28157    True
28158    True
28159    True
Length: 1280, dtype: bool
1280
27520    True
27521    True
27522    True
27523    True
27524    True
     

/usr/local/lib/python3.7/dist-packages/scipy/signal/spectral.py:1966: UserWarning: nperseg = 256 is greater than input length  = 192, using nperseg = 192
  .format(nperseg, input_length))


31360    True
31361    True
31362    True
31363    True
31364    True
         ... 
32635    True
32636    True
32637    True
32638    True
32639    True
Length: 1280, dtype: bool
1280
32000    True
32001    True
32002    True
32003    True
32004    True
         ... 
33275    True
33276    True
33277    True
33278    True
33279    True
Length: 1280, dtype: bool
1280
32640    True
32641    True
32642    True
32643    True
32644    True
         ... 
33915    True
33916    True
33917    True
33918    True
33919    True
Length: 1280, dtype: bool
1280
33280    True
33281    True
33282    True
33283    True
33284    True
         ... 
34555    True
34556    True
34557    True
34558    True
34559    True
Length: 1280, dtype: bool
1280
33920    True
33921    True
33922    True
33923    True
33924    True
         ... 
35195    True
35196    True
35197    True
35198    True
35199    True
Length: 1280, dtype: bool
1280
34560    True
34561    True
34562    True
34563    True
34564    True
     

# Combining Features

In [ ]:
PATH = r"/gdrive/MyDrive/SamsungWork/FinalECGFeatures5SecondsCompleteDF"
EXT = "*.csv"
all_csv_files = [file
                 for path, subdir, files in os.walk(PATH)
                 for file in glob(os.path.join(path, EXT))]
# len(all_csv_files)
column_names=['Mean RR (ms)', 'STD RR/SDNN (ms)', "Mean HR (Kubios' style) (beats/min)", 'Mean HR (beats/min)', 'STD HR (beats/min)', 'Min HR (beats/min)', 'Max HR (beats/min)', 'RMSSD (ms)', 'NNxx', 'pNNxx (%)', 'Power VLF (ms2)', 'Power LF (ms2)', 'Power HF (ms2)', 'Power Total (ms2)', 'LF/HF', 'Peak VLF (Hz)', 'Peak LF (Hz)', 'Peak HF (Hz)', 'Fraction LF (nu)', 'Fraction HF (nu)']

combineddf= pd.DataFrame(columns=column_names) 


In [ ]:
for featuredata in all_csv_files:
      tempdata=pd.read_csv(featuredata)
      combineddf=combineddf.append(tempdata,ignore_index=True)


In [ ]:
combineddf.to_csv(r"/gdrive/MyDrive/SamsungWork/FinalECGFeatures5SecondsCompleteDF/5SecondsCombinedFeatures.csv")


In [ ]:
print(combineddf)

      Mean RR (ms)  STD RR/SDNN (ms)  Mean HR (Kubios' style) (beats/min)  \
0       432.644509        198.277939                           138.681987   
1       428.303571        190.740124                           140.087555   
2       448.809524        205.087262                           133.687003   
3       385.894737        124.204000                           155.482815   
4       422.500000        178.009831                           142.011834   
...            ...               ...                                  ...   
8046    392.606952        138.208996                           152.824599   
8047    392.635135        136.214936                           152.813629   
8048    380.906736        125.434041                           157.518874   
8049    372.920918        117.016407                           160.892020   
8050    389.301075        135.180517                           154.122359   

      Mean HR (beats/min)  STD HR (beats/min)  Min HR (beats/min)  \
0     